In [194]:
from gensim.models import word2vec
import pandas, pymysql
from gensim.models import KeyedVectors
import gensim
import numpy as np

def create_feature_vectors(corpus, doc_id_list):
#     here we use the pre trained model for creating feature vectors
    model = KeyedVectors.load_word2vec_format('GoogleNews-vectors-negative300.bin', binary=True)
    # word_vector = []
    # word_not_in_vocab = []
    for doc in corpus:
        # print(doc)
        word_vector = []
        # word_vector = [model[x] for x in doc.split(' ')]
        for x in doc.split(' '):
            try:
                word_vector.append(model[x])
                # print("---"+str(len(model[x])))
            except KeyError:
                # print("word "+str(x)+" not in vocab")
                # word_not_in_vocab.append(x)
                word_vector.append(np.array([0] * 300))
    # create a list of zeroes

    # print(word_vector)
    #     this word vector is for each document, we need to figure out how to use this word vector further
    # print(word_not_in_vocab)

host = 'webirfacts.csdsyolim34i.us-east-2.rds.amazonaws.com'
port = 3306
username = 'group5'
password = 'aws12345'
dbname = 'facts_8'

# setting up a connection to aws
conn = pymysql.connect(host, user=username,port=port, passwd=password, db=dbname)
conn_cursor = conn.cursor()



# we need to create a corpus first
#get the cleaned extracted text from image from the database
get_clean_data = 'select doc_id, clean_data from clean_text where clean_data is not null or length(clean_data) > 0'
clean_text_df = pandas.read_sql(get_clean_data, con = conn)

corpus = []
doc_id_list = []
for data in clean_text_df.itertuples():
    corpus.append(data[2])
    doc_id_list.append(data[1])
# pass this corpus to the feature vector generator
# create_feature_vectors(corpus)
create_feature_vectors(corpus, doc_id_list)
# print(len(corpus))

In [259]:
print(len(corpus))
print(len(doc_id_list))
clean_text_df.head()

5700
5700


doc_id                                         clean_data
0    2849  drinking many ipas cause boob hop type beer ho...
1    3781                                                   
2    1239  2007 married couple divorce realize cheat onli...
3    2586  cockroach live nine day without head starves d...
4      50  pebble grey spend 7 hour year hiding bathroom ...

# Data split

In [196]:
from sklearn.model_selection import train_test_split

In [260]:
data_sentence = clean_text_df['clean_data']
X_train, X_test = train_test_split(data_sentence, test_size=0.2)
print (X_train.shape)
print (X_test.shape)

(4560,)
(1140,)


In [263]:
data_all = data_sentence

# Tokenazation

In [198]:
import gensim
from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from nltk.stem import WordNetLemmatizer, SnowballStemmer
import numpy as np
import nltk

In [199]:
def preprocess(text):
    result = []
    for token in gensim.utils.simple_preprocess(text):
        if token not in gensim.parsing.preprocessing.STOPWORDS and len(token) > 3:
            result.append(token)
    return result

In [200]:
preprocess('drinking alcohol help stave radioactive poison')

['drinking', 'alcohol', 'help', 'stave', 'radioactive', 'poison']

In [201]:
words = []
for word in X_train:
    word = preprocess(word)
    words.append(word)

In [265]:
#all
words_all = []
for word in data_all:
    word = preprocess(word)
    words.append(word)

In [202]:
print(words[:5])

[['creator', 'tetris', 'brutally', 'murder', 'family', 'receive', 'money', 'game', 'success'], ['kissing', 'hygienic', 'healthy', 'shake', 'hands'], ['pain'], ['similar', 'friend', 'similar', 'romantic', 'partner', 'start', 'relationship'], ['percent', 'believe', 'hard', 'understand', 'pain']]


In [266]:
#all
print(words_all[:5])

[]


In [203]:
processed_docs = X_train.map(preprocess)
processed_docs[:10]

1883    [creator, tetris, brutally, murder, family, re...
4339           [kissing, hygienic, healthy, shake, hands]
5231                                               [pain]
5472    [similar, friend, similar, romantic, partner, ...
5386           [percent, believe, hard, understand, pain]
3396               [thirty, percent, grow, wisdom, teeth]
2422                                     [ennem, abvismh]
3534                                        [point, kiss]
3136                   [woman, england, fall, coma, love]
3466                         [impatient, procrastinators]
Name: clean_data, dtype: object

In [268]:
#all
processed_docs_all = data_all.map(preprocess)
processed_docs[:10]

1883    [creator, tetris, brutally, murder, family, re...
4339           [kissing, hygienic, healthy, shake, hands]
5231                                               [pain]
5472    [similar, friend, similar, romantic, partner, ...
5386           [percent, believe, hard, understand, pain]
3396               [thirty, percent, grow, wisdom, teeth]
2422                                     [ennem, abvismh]
3534                                        [point, kiss]
3136                   [woman, england, fall, coma, love]
3466                         [impatient, procrastinators]
Name: clean_data, dtype: object

# Bag of Words on the Data set

In [350]:
dictionary = gensim.corpora.Dictionary(processed_docs)

In [389]:
#all
dictionary = gensim.corpora.Dictionary(processed_docs_all)

In [352]:
count = 0
for k, v in dictionary.iteritems():
    print(k, v)
    count += 1
    if count > 10:
        break

8445 devil
6119 interpreting
2496 reaction
1988 sarkazein
7380 parade
6101 influence
1037 turned
8114 pana
188 rhino
7521 calment
718 earthquakes


Filter out tokens that appear in

less than 15 documents (absolute number) or
more than 0.5 documents (fraction of total corpus size, not absolute number).
after the above two steps, keep only the first 10000 most frequent tokens.

In [390]:
dictionary.filter_extremes(no_below=2, no_above=0.5, keep_n=10000)

For each document we create a dictionary reporting how many
words and how many times those words appear. Save this to ‘bow_corpus’, then check our selected document earlier.

In [391]:
bow_corpus = [dictionary.doc2bow(doc) for doc in processed_docs]
bow_corpus[3]

[(84, 1), (125, 1), (142, 1), (961, 2), (1261, 1), (1584, 1)]

In [454]:
len(bow_corpus)

4560

In [392]:
bow_doc_3 = bow_corpus[3]
for i in range(len(bow_doc_3)):
    print("Word {} (\"{}\") appears {} time.".format(bow_doc_3[i][0], 
                                               dictionary[bow_doc_3[i][0]], 
bow_doc_3[i][1]))

Word 84 ("start") appears 1 time.
Word 125 ("partner") appears 1 time.
Word 142 ("friend") appears 1 time.
Word 961 ("similar") appears 2 time.
Word 1261 ("relationship") appears 1 time.
Word 1584 ("romantic") appears 1 time.


# TF-IDF 

TF-IDF scores for our first document

In [393]:
from gensim import corpora, models
tfidf = models.TfidfModel(bow_corpus)
corpus_tfidf = tfidf[bow_corpus]
from pprint import pprint
for doc in corpus_tfidf:
    pprint(doc)
    break

[(226, 0.31736723255494864),
 (391, 0.28646551666495224),
 (759, 0.28646551666495224),
 (845, 0.3553899670213806),
 (1365, 0.3979645743074702),
 (1941, 0.3511522748089939),
 (2364, 0.3897627857684745),
 (2409, 0.41863143084037563)]


In [473]:
print('Word index, score:')
print(corpus_tfidf[100][0])

Word index, score:
(141, 0.4893851050077281)


# Running LDA using Bag of Words

In [394]:
lda_model = gensim.models.LdaMulticore(bow_corpus, num_topics=10, id2word=dictionary, passes=2, workers=2)

In [395]:
lda_model.show_topics()

[(0,
  '0.014*"word" + 0.012*"life" + 0.009*"poop" + 0.009*"mean" + 0.007*"know" + 0.007*"depressed" + 0.007*"look" + 0.006*"define" + 0.006*"dict" + 0.006*"away"'),
 (1,
  '0.011*"ability" + 0.009*"woman" + 0.007*"partner" + 0.006*"creative" + 0.006*"school" + 0.006*"friendship" + 0.006*"contain" + 0.006*"staring" + 0.005*"dollar" + 0.005*"strong"'),
 (2,
  '0.015*"percent" + 0.013*"food" + 0.010*"sfact" + 0.009*"child" + 0.008*"want" + 0.008*"life" + 0.008*"high" + 0.006*"drink" + 0.006*"friend" + 0.006*"spend"'),
 (3,
  '0.012*"love" + 0.010*"voice" + 0.010*"coffee" + 0.009*"life" + 0.008*"word" + 0.008*"percent" + 0.008*"good" + 0.006*"year" + 0.006*"wake" + 0.006*"food"'),
 (4,
  '0.015*"water" + 0.013*"year" + 0.011*"percent" + 0.010*"mean" + 0.009*"billion" + 0.007*"word" + 0.007*"body" + 0.006*"honey" + 0.006*"exist" + 0.006*"heart"'),
 (5,
  '0.009*"talk" + 0.009*"percent" + 0.009*"island" + 0.009*"work" + 0.007*"word" + 0.007*"bear" + 0.007*"employee" + 0.006*"food" + 0.006*"

In [396]:
for idx, topic in lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.014*"word" + 0.012*"life" + 0.009*"poop" + 0.009*"mean" + 0.007*"know" + 0.007*"depressed" + 0.007*"look" + 0.006*"define" + 0.006*"dict" + 0.006*"away"
Topic: 1 
Words: 0.011*"ability" + 0.009*"woman" + 0.007*"partner" + 0.006*"creative" + 0.006*"school" + 0.006*"friendship" + 0.006*"contain" + 0.006*"staring" + 0.005*"dollar" + 0.005*"strong"
Topic: 2 
Words: 0.015*"percent" + 0.013*"food" + 0.010*"sfact" + 0.009*"child" + 0.008*"want" + 0.008*"life" + 0.008*"high" + 0.006*"drink" + 0.006*"friend" + 0.006*"spend"
Topic: 3 
Words: 0.012*"love" + 0.010*"voice" + 0.010*"coffee" + 0.009*"life" + 0.008*"word" + 0.008*"percent" + 0.008*"good" + 0.006*"year" + 0.006*"wake" + 0.006*"food"
Topic: 4 
Words: 0.015*"water" + 0.013*"year" + 0.011*"percent" + 0.010*"mean" + 0.009*"billion" + 0.007*"word" + 0.007*"body" + 0.006*"honey" + 0.006*"exist" + 0.006*"heart"
Topic: 5 
Words: 0.009*"talk" + 0.009*"percent" + 0.009*"island" + 0.009*"work" + 0.007*"word" + 0.007*"bear" + 0.

Check the most important words in a topic

In [397]:
lda_model.get_topic_terms(0, topn=3)

[(63, 0.013666662), (367, 0.01168299), (378, 0.0091597745)]

Get top3 most important words for each of the topic

In [398]:
lda_model.print_topics(num_topics=10, num_words=5)

[(0,
  '0.014*"word" + 0.012*"life" + 0.009*"poop" + 0.009*"mean" + 0.007*"know"'),
 (1,
  '0.011*"ability" + 0.009*"woman" + 0.007*"partner" + 0.006*"creative" + 0.006*"school"'),
 (2,
  '0.015*"percent" + 0.013*"food" + 0.010*"sfact" + 0.009*"child" + 0.008*"want"'),
 (3,
  '0.012*"love" + 0.010*"voice" + 0.010*"coffee" + 0.009*"life" + 0.008*"word"'),
 (4,
  '0.015*"water" + 0.013*"year" + 0.011*"percent" + 0.010*"mean" + 0.009*"billion"'),
 (5,
  '0.009*"talk" + 0.009*"percent" + 0.009*"island" + 0.009*"work" + 0.007*"word"'),
 (6,
  '0.015*"dollar" + 0.011*"percent" + 0.010*"blood" + 0.007*"population" + 0.006*"million"'),
 (7,
  '0.015*"dollar" + 0.010*"minute" + 0.009*"risk" + 0.008*"garbage" + 0.008*"school"'),
 (8,
  '0.030*"percent" + 0.010*"minute" + 0.009*"american" + 0.009*"sfaci" + 0.008*"body"'),
 (9,
  '0.012*"best" + 0.011*"bfact" + 0.011*"friend" + 0.011*"dream" + 0.009*"face"')]

In [399]:
cluster_names = {0: 'percent high school', 
                 1: 'life american dream', 
                 2: 'island head risk', 
                 3: 'year hour relationship', 
                 4: 'word mean chocolate',
                 5: 'friend cause blood',
                 6: 'face alcohol second',
                 7: 'billion dollar best',
                 8: 'word woman minute',
                 9: 'minute night food'}
cluster_names

{0: 'percent high school',
 1: 'life american dream',
 2: 'island head risk',
 3: 'year hour relationship',
 4: 'word mean chocolate',
 5: 'friend cause blood',
 6: 'face alcohol second',
 7: 'billion dollar best',
 8: 'word woman minute',
 9: 'minute night food'}

In [400]:
names = ['school', 'life', 'risk','relationship',
         'words', 'friend', 'alcohol', 'money',
         'woman', 'food'
        ]

In [401]:
type(lda_model.print_topics(-1))

list

In [402]:
a = list(lda_model.print_topics(-1)[0])
a[0]

0

In [403]:
index = []
for i in np.arange(10):
    topics = list(lda_model.print_topics(-1)[i])
    topics[0] = names[i]
    index.append(topics)

In [404]:
index

[['school',
  '0.014*"word" + 0.012*"life" + 0.009*"poop" + 0.009*"mean" + 0.007*"know" + 0.007*"depressed" + 0.007*"look" + 0.006*"define" + 0.006*"dict" + 0.006*"away"'],
 ['life',
  '0.011*"ability" + 0.009*"woman" + 0.007*"partner" + 0.006*"creative" + 0.006*"school" + 0.006*"friendship" + 0.006*"contain" + 0.006*"staring" + 0.005*"dollar" + 0.005*"strong"'],
 ['risk',
  '0.015*"percent" + 0.013*"food" + 0.010*"sfact" + 0.009*"child" + 0.008*"want" + 0.008*"life" + 0.008*"high" + 0.006*"drink" + 0.006*"friend" + 0.006*"spend"'],
 ['relationship',
  '0.012*"love" + 0.010*"voice" + 0.010*"coffee" + 0.009*"life" + 0.008*"word" + 0.008*"percent" + 0.008*"good" + 0.006*"year" + 0.006*"wake" + 0.006*"food"'],
 ['words',
  '0.015*"water" + 0.013*"year" + 0.011*"percent" + 0.010*"mean" + 0.009*"billion" + 0.007*"word" + 0.007*"body" + 0.006*"honey" + 0.006*"exist" + 0.006*"heart"'],
 ['friend',
  '0.009*"talk" + 0.009*"percent" + 0.009*"island" + 0.009*"work" + 0.007*"word" + 0.007*"bear" 

In [405]:
for idx, topic in index:
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: school 
Words: 0.014*"word" + 0.012*"life" + 0.009*"poop" + 0.009*"mean" + 0.007*"know" + 0.007*"depressed" + 0.007*"look" + 0.006*"define" + 0.006*"dict" + 0.006*"away"
Topic: life 
Words: 0.011*"ability" + 0.009*"woman" + 0.007*"partner" + 0.006*"creative" + 0.006*"school" + 0.006*"friendship" + 0.006*"contain" + 0.006*"staring" + 0.005*"dollar" + 0.005*"strong"
Topic: risk 
Words: 0.015*"percent" + 0.013*"food" + 0.010*"sfact" + 0.009*"child" + 0.008*"want" + 0.008*"life" + 0.008*"high" + 0.006*"drink" + 0.006*"friend" + 0.006*"spend"
Topic: relationship 
Words: 0.012*"love" + 0.010*"voice" + 0.010*"coffee" + 0.009*"life" + 0.008*"word" + 0.008*"percent" + 0.008*"good" + 0.006*"year" + 0.006*"wake" + 0.006*"food"
Topic: words 
Words: 0.015*"water" + 0.013*"year" + 0.011*"percent" + 0.010*"mean" + 0.009*"billion" + 0.007*"word" + 0.007*"body" + 0.006*"honey" + 0.006*"exist" + 0.006*"heart"
Topic: friend 
Words: 0.009*"talk" + 0.009*"percent" + 0.009*"island" + 0.009*"work" + 0

# Running LDA using TF-IDF

In [406]:
lda_model_tfidf = gensim.models.LdaMulticore(corpus_tfidf, num_topics=10, id2word=dictionary, passes=2, workers=4)
for idx, topic in lda_model_tfidf.print_topics(-1):
    print('Topic: {} Word: {}'.format(idx, topic))

Topic: 0 Word: 0.009*"percent" + 0.008*"dollar" + 0.006*"minute" + 0.004*"high" + 0.004*"kill" + 0.004*"week" + 0.004*"friend" + 0.004*"date" + 0.003*"fall" + 0.003*"risk"
Topic: 1 Word: 0.004*"percent" + 0.004*"music" + 0.003*"math" + 0.003*"listen" + 0.003*"blood" + 0.003*"help" + 0.003*"head" + 0.003*"urine" + 0.003*"depression" + 0.003*"child"
Topic: 2 Word: 0.011*"percent" + 0.005*"bfact" + 0.005*"relationship" + 0.005*"stress" + 0.004*"second" + 0.004*"good" + 0.003*"happy" + 0.003*"million" + 0.003*"born" + 0.003*"movie"
Topic: 3 Word: 0.007*"percent" + 0.006*"friend" + 0.004*"reason" + 0.003*"music" + 0.003*"level" + 0.003*"anxiety" + 0.003*"talk" + 0.003*"adult" + 0.003*"green" + 0.003*"lose"
Topic: 4 Word: 0.006*"love" + 0.004*"percent" + 0.004*"think" + 0.004*"work" + 0.004*"word" + 0.004*"year" + 0.004*"look" + 0.003*"live" + 0.003*"come" + 0.003*"phone"
Topic: 5 Word: 0.006*"percent" + 0.005*"life" + 0.005*"word" + 0.004*"night" + 0.003*"dict" + 0.003*"depression" + 0.003*

# Evaluation with bag of words

In [407]:
processed_docs[3]

['cockroach', 'live', 'head', 'starves', 'death']

In [408]:
for index, score in sorted(lda_model[bow_corpus[3]], key=lambda tup: -1*tup[1]):
    print("\nScore: {}\t \nTopic: {}".format(score, lda_model.print_topic(index, 10)))


Score: 0.47492071986198425	 
Topic: 0.030*"percent" + 0.010*"minute" + 0.009*"american" + 0.009*"sfaci" + 0.008*"body" + 0.007*"head" + 0.006*"money" + 0.006*"song" + 0.005*"male" + 0.005*"alcohol"

Score: 0.24240486323833466	 
Topic: 0.015*"dollar" + 0.010*"minute" + 0.009*"risk" + 0.008*"garbage" + 0.008*"school" + 0.008*"hour" + 0.007*"second" + 0.007*"blue" + 0.007*"think" + 0.007*"friend"

Score: 0.19514721632003784	 
Topic: 0.012*"best" + 0.011*"bfact" + 0.011*"friend" + 0.011*"dream" + 0.009*"face" + 0.008*"work" + 0.008*"think" + 0.008*"hour" + 0.007*"blind" + 0.007*"chocolate"

Score: 0.01250560861080885	 
Topic: 0.011*"ability" + 0.009*"woman" + 0.007*"partner" + 0.006*"creative" + 0.006*"school" + 0.006*"friendship" + 0.006*"contain" + 0.006*"staring" + 0.005*"dollar" + 0.005*"strong"

Score: 0.012505173683166504	 
Topic: 0.012*"love" + 0.010*"voice" + 0.010*"coffee" + 0.009*"life" + 0.008*"word" + 0.008*"percent" + 0.008*"good" + 0.006*"year" + 0.006*"wake" + 0.006*"food"


# Evaluation with TF-IDF 

In [409]:
for index, score in sorted(lda_model_tfidf[bow_corpus[3]], key=lambda tup: -1*tup[1]):
    print("\nScore: {}\t \nTopic: {}".format(score, lda_model_tfidf.print_topic(index, 10)))


Score: 0.8874673843383789	 
Topic: 0.004*"year" + 0.004*"friend" + 0.004*"percent" + 0.003*"love" + 0.003*"ability" + 0.003*"game" + 0.003*"thing" + 0.003*"bfact" + 0.003*"sfacicom" + 0.003*"product"

Score: 0.012506727129220963	 
Topic: 0.011*"percent" + 0.005*"bfact" + 0.005*"relationship" + 0.005*"stress" + 0.004*"second" + 0.004*"good" + 0.003*"happy" + 0.003*"million" + 0.003*"born" + 0.003*"movie"

Score: 0.012504364363849163	 
Topic: 0.004*"percent" + 0.004*"music" + 0.003*"math" + 0.003*"listen" + 0.003*"blood" + 0.003*"help" + 0.003*"head" + 0.003*"urine" + 0.003*"depression" + 0.003*"child"

Score: 0.012504364363849163	 
Topic: 0.007*"percent" + 0.006*"friend" + 0.004*"reason" + 0.003*"music" + 0.003*"level" + 0.003*"anxiety" + 0.003*"talk" + 0.003*"adult" + 0.003*"green" + 0.003*"lose"

Score: 0.012503726407885551	 
Topic: 0.006*"percent" + 0.004*"hour" + 0.004*"sfact" + 0.004*"live" + 0.003*"life" + 0.003*"dollar" + 0.003*"love" + 0.003*"calorie" + 0.003*"burn" + 0.003*"fo

# Running model on test data

In [410]:
array = []
for i in range(len(X_test)):
    bow_vector = dictionary.doc2bow(preprocess(np.array(X_test)[i]))
    array.append(bow_vector)

In [411]:
#all
array = []
for i in range(len(data_sentence)):
    bow_vector = dictionary.doc2bow(preprocess(np.array(data_sentence)[i]))
    array.append(bow_vector)

In [412]:
bow_vector = dictionary.doc2bow(preprocess(np.array(X_test)[0]))

In [413]:
#all
bow_vector = dictionary.doc2bow(preprocess(np.array(data_sentence)[0]))

In [414]:
type(bow_vector)

list

In [415]:
data_sentence.index[0]

0

In [416]:
result=[]
for i in range(len(array)):
    print('element')
    print(array[i])
    for index, score in sorted(lda_model[array[i]], key=lambda tup: -1*tup[1]):
        print("Score: {}\t Topic: {}".format(score, index))
        result.append([data_sentence.index[i],index, score]) 

element
[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1)]
Score: 0.416936457157135	 Topic: 0
Score: 0.330995112657547	 Topic: 5
Score: 0.18202434480190277	 Topic: 8
Score: 0.010007834993302822	 Topic: 2
Score: 0.010006727650761604	 Topic: 4
Score: 0.010006153024733067	 Topic: 3
Score: 0.010006073862314224	 Topic: 1
Score: 0.010006014257669449	 Topic: 9
Score: 0.010005990043282509	 Topic: 6
Score: 0.010005303658545017	 Topic: 7
element
[]
Score: 0.10000000149011612	 Topic: 0
Score: 0.10000000149011612	 Topic: 1
Score: 0.10000000149011612	 Topic: 2
Score: 0.10000000149011612	 Topic: 3
Score: 0.10000000149011612	 Topic: 4
Score: 0.10000000149011612	 Topic: 5
Score: 0.10000000149011612	 Topic: 6
Score: 0.10000000149011612	 Topic: 7
Score: 0.10000000149011612	 Topic: 8
Score: 0.10000000149011612	 Topic: 9
element
[(9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1)]
Score: 0.7277626991271973	 Topic: 2
Score: 0.15789051353931427	 Topic: 1
Score: 0.01429753564298153	 To

In [417]:
#all
result=[]
for i in range(len(array)):
    print('element')
    print(array[i])
    for index, score in sorted(lda_model[array[i]], key=lambda tup: -1*tup[1]):
        print("Score: {}\t Topic: {}".format(score, index))
        result.append([data_sentence.index[i],index, score]) 

element
[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1)]
Score: 0.41695496439933777	 Topic: 0
Score: 0.3310091495513916	 Topic: 5
Score: 0.1819918155670166	 Topic: 8
Score: 0.010007834061980247	 Topic: 2
Score: 0.01000672671943903	 Topic: 4
Score: 0.010006153024733067	 Topic: 3
Score: 0.01000607293099165	 Topic: 1
Score: 0.010006013326346874	 Topic: 9
Score: 0.010005989111959934	 Topic: 6
Score: 0.010005302727222443	 Topic: 7
element
[]
Score: 0.10000000149011612	 Topic: 0
Score: 0.10000000149011612	 Topic: 1
Score: 0.10000000149011612	 Topic: 2
Score: 0.10000000149011612	 Topic: 3
Score: 0.10000000149011612	 Topic: 4
Score: 0.10000000149011612	 Topic: 5
Score: 0.10000000149011612	 Topic: 6
Score: 0.10000000149011612	 Topic: 7
Score: 0.10000000149011612	 Topic: 8
Score: 0.10000000149011612	 Topic: 9
element
[(9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1)]
Score: 0.7277615070343018	 Topic: 2
Score: 0.15789078176021576	 Topic: 1
Score: 0.014298433437943459	 T

In [419]:
import pandas as pd

In [420]:
pd_result = pd.DataFrame(result)

In [421]:
pd_result.columns = ["doc_id", "topic", "score"]

In [422]:
pd_result.shape

(53102, 3)

In [423]:
most_frequent = pd_result['topic']
most_frequent.columns = ['most_frequent']
most_frequent.shape

(53102,)

In [424]:
pd_big = pd_result.join(most_frequent,lsuffix='_one_word', rsuffix='_three_words')
pd_result = pd_big

In [425]:
pd_result.head()

doc_id  topic_one_word     score  topic_three_words
0       0               0  0.416955                  0
1       0               5  0.331009                  5
2       0               8  0.181992                  8
3       0               2  0.010008                  2
4       0               4  0.010007                  4

In [426]:
pd_result['topic_three_words'] = pd_result['topic_three_words'].map({0: 'percent high school', 
                 1: 'life american dream', 
                 2: 'island head risk', 
                 3: 'year hour relationship', 
                 4: 'word mean chocolate',
                 5: 'friend cause blood',
                 6: 'face alcohol second',
                 7: 'billion dollar best',
                 8: 'word woman minute',
                 9: 'minute night food'})

In [427]:
pd_result['topic_one_word'] = pd_result['topic_one_word'].map({0: 'school', 
                 1: 'life', 
                 2: 'risk', 
                 3: 'relationships', 
                 4: 'words',
                 5: 'friend',
                 6: 'alcohol',
                 7: 'money',
                 8: 'woman',
                 9: 'food'})

In [428]:
pd_result2 = pd_result[pd_result['score']>0.3]
pd_result2.shape

(5898, 4)

In [333]:
pd_result.to_csv('target_matrix_all', sep='\t', encoding='utf-8')

In [341]:
pd_result.to_json('target_matrix_all_json',orient='table')

In [429]:
target_list = list(pd_result)

In [430]:
host = 'webirfacts.csdsyolim34i.us-east-2.rds.amazonaws.com'
port = 3306
username = 'group5'
password = 'aws12345'
dbname = 'facts_8'

In [431]:
connection = pymysql.connect(host='webirfacts.csdsyolim34i.us-east-2.rds.amazonaws.com',
                             user='group5',
                             password='aws12345',
                             db='facts_8')

In [349]:
for data in pd_result2.itertuples():
    with connection.cursor() as cursor:
        insert_tuple = (int(data[1]), str(data[2]), float(data[3]), str(data[4]))
        sql = "INSERT INTO target_matrix_all (doc_id, topic_one_word, score, topic_three_words) VALUES (%s, %s, %s, %s)"
        #executemany
        cursor.execute(sql, insert_tuple)
connection.commit()

In [258]:
pd_result.columns

Index(['doc_id', 'topic_one_word', 'score', 'topic_three_words'], dtype='object')

In [446]:
# Import required packages
import numpy as np
import logging
import pyLDAvis.gensim
import json
import warnings
warnings.filterwarnings('ignore')  # To ignore all warnings that arise here to enhance clarity

from gensim.models.coherencemodel import CoherenceModel
from gensim.models.ldamodel import LdaModel
from gensim.corpora.dictionary import Dictionary
from numpy import array

p_df = data_sentence
# Convert to array
docs =array(p_df)
# Define function for tokenize and lemmatizing
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.tokenize import RegexpTokenizer

def docs_preprocessor(docs):
    tokenizer = RegexpTokenizer(r'\w+')
    for idx in range(len(docs)):
        docs[idx] = docs[idx].lower()  # Convert to lowercase.
        docs[idx] = tokenizer.tokenize(docs[idx])  # Split into words.

    # Remove numbers, but not words that contain numbers.
    docs = [[token for token in doc if not token.isdigit()] for doc in docs]
    
    # Remove words that are only one character.
    docs = [[token for token in doc if len(token) > 3] for doc in docs]
    
    # Lemmatize all words in documents.
    lemmatizer = WordNetLemmatizer()
    docs = [[lemmatizer.lemmatize(token) for token in doc] for doc in docs]
  
    return docs
# Perform function on our document
docs = docs_preprocessor(docs)
#Create Biagram & Trigram Models 
from gensim.models import Phrases
# Add bigrams and trigrams to docs,minimum count 10 means only that appear 10 times or more.
bigram = Phrases(docs, min_count=10)
trigram = Phrases(bigram[docs])

for idx in range(len(docs)):
    for token in bigram[docs[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            docs[idx].append(token)
    for token in trigram[docs[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            docs[idx].append(token)
#Remove rare & common tokens 
# Create a dictionary representation of the documents.
dictionary = Dictionary(docs)
dictionary.filter_extremes(no_below=10, no_above=0.2)
#Create dictionary and corpus required for Topic Modeling
corpus = [dictionary.doc2bow(doc) for doc in docs]
print('Number of unique tokens: %d' % len(dictionary))
print('Number of documents: %d' % len(corpus))
print(corpus[:1])

Number of unique tokens: 802
Number of documents: 5700
[[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 1)]]


In [447]:
# Set parameters.
num_topics = 10
chunksize = 500 
passes = 20 
iterations = 400
eval_every = 1  

# Make a index to word dictionary.
temp = dictionary[0]  # only to "load" the dictionary.
id2word = dictionary.id2token

lda_model = LdaModel(corpus=corpus, id2word=id2word, chunksize=chunksize, \
                       alpha='auto', eta='auto', \
                       iterations=iterations, num_topics=num_topics, \
                       passes=passes, eval_every=eval_every)
# Print the Keyword in the 5 topics
print(lda_model.print_topics())

[(0, '0.063*"friend" + 0.048*"8dict_define" + 0.045*"good" + 0.040*"name" + 0.039*"give" + 0.032*"become" + 0.030*"also" + 0.029*"anxiety" + 0.028*"hand" + 0.027*"least"'), (1, '0.049*"take" + 0.043*"live" + 0.040*"minute" + 0.032*"last" + 0.031*"research_show" + 0.030*"research" + 0.029*"blood" + 0.029*"live_longer" + 0.027*"stress" + 0.026*"longer"'), (2, '0.055*"high" + 0.039*"school" + 0.038*"work" + 0.038*"cause" + 0.037*"high_school" + 0.034*"body" + 0.034*"alcohol" + 0.032*"sfact" + 0.030*"keep" + 0.027*"tell"'), (3, '0.047*"food" + 0.041*"drink" + 0.038*"water" + 0.028*"reduce_risk" + 0.028*"risk" + 0.027*"often" + 0.026*"reduce" + 0.026*"best" + 0.026*"eating" + 0.025*"music"'), (4, '0.051*"think" + 0.034*"lose" + 0.033*"help" + 0.032*"pain" + 0.029*"sfaci" + 0.028*"girl" + 0.028*"want" + 0.026*"fall_asleep" + 0.025*"fall" + 0.024*"feeling"'), (5, '0.044*"cost_dollar" + 0.043*"show" + 0.035*"increase" + 0.032*"around" + 0.029*"make" + 0.028*"genius_hack" + 0.025*"relationship"

In [448]:
# Compute Coherence Score using c_v
coherence_model_lda = CoherenceModel(model=lda_model, texts=docs, dictionary=dictionary, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Coherence Score:  0.5505721257733875


In [449]:
# Compute Coherence Score using UMass
coherence_model_lda = CoherenceModel(model=lda_model, texts=docs, dictionary=dictionary, coherence="u_mass")
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Coherence Score:  -15.977162911575226


In [450]:
def compute_coherence_values(dictionary, corpus, texts, limit, start=2, step=3):
    """
    Compute c_v coherence for various number of topics

    Parameters:
    ----------
    dictionary : Gensim dictionary
    corpus : Gensim corpus
    texts : List of input texts
    limit : Max num of topics

    Returns:
    -------
    model_list : List of LDA topic models
    coherence_values : Coherence values corresponding to the LDA model with respective number of topics
    """
    coherence_values = []
    model_list = []
    for num_topics in range(start, limit, step):
        model=LdaModel(corpus=corpus, id2word=dictionary, num_topics=num_topics)
        model_list.append(model)
        coherencemodel = CoherenceModel(model=model, texts=texts, dictionary=dictionary, coherence='c_v')
        coherence_values.append(coherencemodel.get_coherence())

    return model_list, coherence_values

In [451]:
model_list, coherence_values = compute_coherence_values(dictionary=dictionary, corpus=corpus, texts=docs, start=2, limit=40, step=6)
# Show graph
import matplotlib.pyplot as plt
limit=40; start=2; step=6;
x = range(start, limit, step)
plt.plot(x, coherence_values)
plt.xlabel("Num Topics")
plt.ylabel("Coherence score")
plt.legend(("coherence_values"), loc='best')
plt.show()